## Table of Contents
* [Dependencies](#Dependnecies)
* [Face Cropping](#faceCropping)
    * [Face Cropping Examples](#cropExamples)
* [Enhance Faces](#enhanceFaces)
    * [Enhance Examples](#enhanceExamples)
* [Align Faces](#alignFaces)
    * [Align Examples](#alignExamples)
* [Face Aging](#faceAging)
    * [Face Aging Examples](#faceAgeExamples)
* [Age Images in Database](#agedb)

## Dependencies <a class="anchor" id="Dependnecies"></a>

In order to run the code, you need to clone into your root director:
- https://github.com/eladrich/pixel2style2pixel
- https://github.com/AbuAbdULLAH-MuhammadAli/FaceAgingStyleGANs

From https://github.com/davisking/dlib-models download the models (you may have to change the paths in the code):
- mmod_human_face_detector.dat (use to detect face)
- shape_predictor_68_face_landmarks.dat (use to detect face)

From https://drive.google.com/file/d/1pJ_T-V1dpb1ewoEra1TGSWl5e6H7M4NN/view download:
- RRDB_ESRGAN_x4.pth  (use to enhance image)

In [1]:
import os
os.chdir('pixel2style2pixel')

In [2]:
from argparse import Namespace
import time
import sys
import pprint
import numpy as np
from PIL import Image
import torch
import torchvision.transforms as transforms
import dlib

sys.path.append(".")
sys.path.append("..")

# from datasets import augmentations
from utils.common import tensor2im, log_input_image
from pixel2style2pixel.models.psp import pSp

#%load_ext autoreload
#%autoreload 2

import cv2
import matplotlib.pyplot as plt 
import dlib
import os.path as osp
import glob
import numpy as np
import Enhancement.RRDBNet_arch as arch
from IPython import display
from tqdm import tqdm
import matplotlib

device = torch.device("cpu")

## 1. Crop Faces with Bounding Box <a class="anchor" id="faceCropping"></a>


In [3]:
%matplotlib inline
#be sure to download mmod_human_face_detector.dat
face_detector_path = cnn_model_path = '../dlib_model/mmod_human_face_detector.dat' #change for your path
cnn_face_detector = dlib.cnn_face_detection_model_v1(face_detector_path)

def detect_crop_face(img, display=False):
    """crops face in photo
    args:
        img- path to image
        display- use for debugging, will display output
    returns:
        image as a numpy array
    """
    image = cv2.imread(img)
    scale_percent = 10 # percent of original size
    width = int(image.shape[1] * scale_percent / 100)
    height = int(image.shape[0] * scale_percent / 100)
    dim = (width, height)
    # resize image
    image = cv2.resize(image, dim, interpolation = cv2.INTER_AREA)
    output_image = image.copy()
    imgRGB = cv2.cvtColor(image,cv2.COLOR_BGR2RGB)
    results = cnn_face_detector(imgRGB,upsample_num_times =2)
    
    for bbox in results:
        x1 = bbox.rect.left()
        y1 = bbox.rect.top()
        x2 = bbox.rect.right()
        y2 = bbox.rect.bottom()
        w = x2-x1
        h = y2-y1
        
        x_adj = int(0.5*w )
        y_adj = int(0.5*h)
        x1_adj = x1-x_adj
        y1_adj = y1-y_adj
        x2_adj = x2+x_adj
        y2_adj = y2+y_adj
        points_adjust =[x1_adj,y1_adj,x2_adj,y2_adj]
        
        if x1_adj < 0:
            x1_adj = 0
        if y1_adj < 0:
            y1_adj = 0
        
        cv2.rectangle(output_image, pt1=(x1_adj,y1_adj), pt2=(x2_adj,y2_adj), color=(0, 0, 255), thickness=2)  
        output_image = output_image[y1_adj:y2_adj,x1_adj:x2_adj]
    if display:
        plt.imshow(cv2.cvtColor(output_image,cv2.COLOR_BGR2RGB))
        plt.show()
    path = f'atfalmafkoda_unzip/test_crop/face_crop{img}'
    #cv2.imwrite(path,output)
    return output_image

## 2. Enhance Faces<a class="anchor" id="enhanceFaces"></a>

In [4]:
def enhance_face(img):
    """enhances image by using super resolution
    args:
        img- numpy array representing an image
    output:
        numpy array representing an image
    """
    model_path = '../Enhancement/models/RRDB_ESRGAN_x4.pth' 
    device = torch.device('cuda')  # if you want to run on CPU, change 'cuda' -> cpu
    # device = torch.device('cpu')

    model = arch.RRDBNet(3, 3, 64, 23, gc=32)
    model.load_state_dict(torch.load(model_path), strict=True)
    model.eval()
    model = model.to(device)
    
    # following commented code was used in testing
    # for path in glob.glob(test_img_folder):
    # base = osp.splitext(osp.basename(img_path))[0]
    # read images
    # img = cv2.imread(img_path, cv2.IMREAD_COLOR)
    output = None
    img = img * 1.0 / 255
    img = torch.from_numpy(np.transpose(img[:, :, [2, 1, 0]], (2, 0, 1))).float()
    img_LR = img.unsqueeze(0)
    img_LR = img_LR.to(device)

    with torch.no_grad():
        output = model(img_LR).data.squeeze().float().cpu().clamp_(0, 1).numpy()
    output = np.transpose(output[[2, 1, 0], :, :], (1, 2, 0))
    output = (output * 255.0).round()
    # cv2.imwrite('Enhancement/results/{:s}_rlt.png'.format(base), output)
    return output

## 3. Align Faces <a class="anchor" id="alignFaces"></a>

In [5]:
#script verision of aligning (frontalizing) face code is available as align.py

In [6]:
#P2S2P documentation for details
experiment_type = 'ffhq_frontalize' 
EXPERIMENT_DATA_ARGS = {
    "ffhq_frontalize": {
        "model_path": "pretrained_models/psp_ffhq_frontalization.pt",
        "image_path": "notebooks/images/input_img.jpg",
        "transform": transforms.Compose([
            transforms.Resize((256, 256)),
            transforms.ToTensor(),
            transforms.Normalize([0.5, 0.5, 0.5], [0.5, 0.5, 0.5])])
    },

}
EXPERIMENT_ARGS = EXPERIMENT_DATA_ARGS[experiment_type]

In [7]:
model_path = EXPERIMENT_ARGS['model_path']
ckpt = torch.load(model_path, map_location='cpu')

In [8]:
opts = ckpt['opts']
pprint.pprint(opts)

{'batch_size': 8,
 'board_interval': 50,
 'checkpoint_path': None,
 'dataset_type': 'ffhq_frontalize',
 'device': 'cuda:0',
 'encoder_type': 'GradualStyleEncoder',
 'exp_dir': '',
 'id_lambda': 1.0,
 'image_interval': 100,
 'input_nc': 3,
 'l2_lambda': 0.001,
 'l2_lambda_crop': 0.01,
 'label_nc': 0,
 'learning_rate': 0.0001,
 'lpips_lambda': 0.08,
 'lpips_lambda_crop': 0.8,
 'max_steps': 80000,
 'optim_name': 'ranger',
 'resize_factors': None,
 'save_interval': 5000,
 'start_from_latent_avg': True,
 'stylegan_weights': '',
 'test_batch_size': 8,
 'test_workers': 2,
 'train_decoder': False,
 'val_interval': 2500,
 'w_norm_lambda': 0.005,
 'workers': 8}


In [9]:
opts['checkpoint_path'] = model_path
if 'learn_in_w' not in opts:
    opts['learn_in_w'] = False
if 'output_size' not in opts:
    opts['output_size'] = 1024

In [10]:
opts = Namespace(**opts)
net = pSp(opts)
net.eval()
net.cuda()
print('Model successfully loaded!')

Loading pSp from checkpoint: pretrained_models/psp_ffhq_frontalization.pt
Model successfully loaded!


In [11]:
#next two functions are helper functions defined by psp notebook
def run_alignment(image_path):
    """helper for frontalize adapted from PSP"""
    from scripts.align_all_parallel import align_face
    
    predictor = dlib.shape_predictor("../shape_predictor_68_face_landmarks.dat")
    aligned_image = align_face(filepath=image_path, predictor=predictor)
    print("Aligned image has shape: {}".format(aligned_image.size))
    return aligned_image


def run_on_batch(inputs, net, latent_mask=None):
    """helper for frontalize adapted from PSP"""
    if latent_mask is None:
        result_batch = net(inputs.to("cuda").float(), randomize_noise=False)
    else:
        result_batch = []
        for image_idx, input_image in enumerate(inputs):
            # get latent vector to inject into our input image
            vec_to_inject = np.random.randn(1, 512).astype('float32')
            _, latent_to_inject = net(torch.from_numpy(vec_to_inject).to("cuda"),
                                      input_code=True,
                                      return_latents=True)
            # get output image with injected style vector
            res = net(input_image.unsqueeze(0).to("cuda").float(),
                      latent_mask=latent_mask,
                      inject_latent=latent_to_inject)
            result_batch.append(res)
        result_batch = torch.cat(result_batch, dim=0)
    return result_batch

#packaging the aligning face into one function
def frontalize(img, net, display=True):
    """frontalize images with psp
    input:
        img- path to image
        net- network optimizer 
    output:
        frontalized image
    """
    original_image = Image.open(img)
    original_image = original_image.convert("RGB")
    original_image.resize((256, 256))
    
    detector = dlib.get_frontal_face_detector()

    img_test = dlib.load_rgb_image(img)
    dets = detector(img_test, 1)
    
    if len(dets) > 0:
        input_image = run_alignment(img)
        input_image.resize((256, 256))
    else:
        input_image = original_image
    
    img_transforms = EXPERIMENT_ARGS['transform']
    transformed_image = img_transforms(input_image)
    
    latent_mask = None
    with torch.no_grad():
        tic = time.time()
        result_image = run_on_batch(transformed_image.unsqueeze(0), net, latent_mask)[0]
        toc = time.time()
        print('Inference took {:.4f} seconds.'.format(toc - tic))
    
    input_vis_image = log_input_image(transformed_image, opts)
    output_image = tensor2im(result_image)
    if display:
        res = np.concatenate([np.array(input_vis_image.resize((256, 256))),
                          np.array(output_image.resize((256, 256)))], axis=1)
    else:
        res = np.concatenate([np.array(output_image.resize((256, 256)))], axis=1)
    res_image = Image.fromarray(res)
    return res_image
    

## 4. Pass through FaceAgingGAN<a class="anchor" id="faceAging"></a>

In [12]:
import os
os.chdir('../FaceAgingStyleGANs')

from collections import OrderedDict
from options.test_options import TestOptions
from data.data_loader import CreateDataLoader
from FaceAgingStyleGANs.models.models import create_model
import util.util as util
from util.visualizer import Visualizer

opt = TestOptions().parse(save=False)
opt.display_id = 0 # do not launch visdom
opt.gpu_ids = 0, 1
opt.nThreads = 1   # test code only supports nThreads = 1
opt.batchSize = 1  # test code only supports batchSize = 1
opt.serial_batches = True  # no shuffle
opt.no_flip = True  # no flip
opt.in_the_wild = True # This triggers preprocessing of in the wild images in the dataloader
opt.traverse = True # This tells the model to traverse the latent space between anchor classes
#opt.interp_step = 0.05 # this controls the number of images to interpolate between anchor classes

------------ Options -------------
activation: lrelu
batchSize: 1
checkpoints_dir: ./checkpoints
compare_to_trained_class: 1
compare_to_trained_outputs: False
conv_weight_norm: True
dataroot: ./datasets/males/
debug_mode: False
decoder_norm: pixel
deploy: False
display_id: 1
display_port: 8097
display_single_pane_ncols: 6
display_winsize: 256
fineSize: 256
full_progression: False
gen_dim_per_style: 50
gpu_ids: [0]
how_many: 50
id_enc_norm: pixel
image_path_file: None
in_the_wild: False
input_nc: 3
interp_step: 0.5
isTrain: False
loadSize: 256
make_video: False
max_dataset_size: inf
nThreads: 1
n_adaptive_blocks: 4
n_downsample: 2
name: debug
ngf: 64
no_cond_noise: False
no_flip: False
no_moving_avg: False
normalize_mlp: True
ntest: inf
output_nc: 3
phase: test
random_seed: -1
resize_or_crop: resize_and_crop
results_dir: ./results/
serial_batches: False
sort_classes: True
sort_order: ['0-2', '3-6', '7-9', '15-19', '30-39', '50-69']
trained_class_jump: 1
traverse: False
use_modulated_con

usage: ipykernel_launcher.py [-h] [--name NAME] [--gpu_ids GPU_IDS]
                             [--checkpoints_dir CHECKPOINTS_DIR]
                             [--batchSize BATCHSIZE] [--loadSize LOADSIZE]
                             [--fineSize FINESIZE] [--input_nc INPUT_NC]
                             [--output_nc OUTPUT_NC] [--dataroot DATAROOT]
                             [--sort_classes SORT_CLASSES]
                             [--sort_order SORT_ORDER]
                             [--resize_or_crop RESIZE_OR_CROP]
                             [--serial_batches] [--no_flip]
                             [--nThreads NTHREADS]
                             [--max_dataset_size MAX_DATASET_SIZE]
                             [--display_single_pane_ncols DISPLAY_SINGLE_PANE_NCOLS]
                             [--display_winsize DISPLAY_WINSIZE]
                             [--display_port DISPLAY_PORT]
                             [--display_id DISPLAY_ID]
                         

In [13]:
#!python download_models.py

In [14]:
#wrapper function for aging the face
def age_face(img, opt, gender, d, front):
    """age face with AgeGAN
    input:
        img- path to image
        opt- network optimizers
        gender- gender of person in photo
        d- current directory
        front- bool; True for frontalized
    output:
        path to aged images
    """
    data_loader = CreateDataLoader(opt)
    dataset = data_loader.load_data()
    visualizer = Visualizer(opt)
    
    if gender == 'male':
        opt.name = 'males_model'
    else: 
        opt.name = 'females_model' 
    
    model = create_model(opt)
    model = model.to()
    model.eval()
    
    data = dataset.dataset.get_item_from_path(img)
    visuals = model.inference(data)
    
    #os.makedirs('results', exist_ok=True)
    if front:
        d = d.rstrip(os.path.basename(d))
        out_path = d+"front"+os.path.basename(img)
    else:
        d = d.rstrip(os.path.basename(d))
        out_path = d+os.path.basename(img)
    print("saved aged faces", out_path)
    visualizer.save_images_deploy(visuals, out_path)
    #visualizer.save_row_image(visuals, out_path, traverse=True)
    return out_path

## Pipeline Run <a class="anchor" id="pipelineRun"></a>

In [19]:
import tempfile
from IPython import display
from PIL import Image
import os
#os.environ['KMP_DUPLICATE_LIB_OK']='True'
#os.environ['CUDA_VISIBLE_DEVICES']='0, 1'
#os.environ['TF_ENABLE_ONEDNN_OPTS']='0'
from deepface import DeepFace
import pandas as pd
device = torch.device("cpu")

#alternatively
def inference(img_path, opt, detect=True, enhance=True, align=True):
    """run the pipeline
    input:
        img_path- path to image
        opt- network optimizer for agefaceGAN
        detect- bool; if you want to crop face
        enhance- bool; if you want to enhance face
        align- bool; if you want to frontalize face
    output:
        path to aged image
    """
    if detect:
        img = detect_crop_face(img_path)
    if enhance:
        img = enhance_face(img)
    img = img.astype(np.uint8)
    with tempfile.TemporaryDirectory() as tmpdirname:
        print('created temporary directory', tmpdirname)
        if align:
            cv2.imwrite(os.path.join(tmpdirname, os.path.basename(img_path)),img)
            img = frontalize(os.path.join(tmpdirname, os.path.basename(img_path)), net, display=False)
            img.save(os.path.join(tmpdirname, os.path.basename(img_path)), "JPEG")
            img.save(os.path.join(img_path.strip(os.path.basename(img_path)),
                                  "frontalized_"+os.path.basename(img_path)), "JPEG")
            print("saved frontalized img")
        else:
            cv2.imwrite(os.path.join(tmpdirname, os.path.basename(img_path)),img)
        
        #detect gender
        genders = {'Man':'male', 'Woman':'female'}
        g = DeepFace.analyze(os.path.join(tmpdirname, os.path.basename(img_path)), detector_backend="mtcnn")
        g = g[0]['dominant_gender']
        print(genders[g])
#         print("path!!!", os.path.join(tmpdirname, os.path.basename(img_path)))
        out = age_face(os.path.join(tmpdirname, os.path.basename(img_path)), opt, genders[g], img_path, align)
    return out

In [20]:
torch.cuda.empty_cache()

In [21]:
from pynvml import *
nvmlInit()
ngpus = nvmlDeviceGetCount()
for i in range(ngpus):
    handle = nvmlDeviceGetHandleByIndex(i)
    gpu_util = nvmlDeviceGetUtilizationRates(handle).gpu
    print('GPU %d Utilization = %d%%' % (i, gpu_util))

GPU 0 Utilization = 0%
GPU 1 Utilization = 0%
GPU 2 Utilization = 0%
GPU 3 Utilization = 0%


# Age Images in Database <a class="anchor" id="agedb"></a>

In [22]:
# the following code ages and frontalizes all of the images inside the database
# outer_folder_path is path to database
# database should be structured as:
# Database
#     PersonX
#       -img1
#       -img2
#     PersonY
#       -img1

outer_folder_path = "/projectnb/sparkgrp/ml-atfal-mafkoda-grp/atfalmafkoda_unzip/database3"
for d in os.listdir(outer_folder_path):
    if not os.path.isdir(outer_folder_path+"/"+d):
        continue
    files = os.listdir(outer_folder_path+"/"+d)
    sub = 'tex_trans_to_class'
    if any(sub in files for files in files):
        continue
    if d != ".ipynb_checkpoints":
        for f in os.listdir(outer_folder_path+"/"+d):
            if not f.startswith('.'):
                path = os.path.join(outer_folder_path+"/"+d,f)
                print("path", path)
                try:
                    out = inference(path, opt, enhance=False)
                except RuntimeError: 
                    print("skipping, no face detected")
                    continue
                except ValueError:
                    print("skipping, no face detected")
                    continue

                try: 
                    out2 = inference(path, opt, enhance=False, align=False)
                except RuntimeError :
                    print("skipping, no face detected")
                    continue
                except ValueError:
                    print("skipping, no face detected")
                    continue
                    

path /projectnb/sparkgrp/ml-atfal-mafkoda-grp/atfalmafkoda_unzip/database3/person78/slice_01_01.jpg
created temporary directory /scratch/7405901.1.cds-gpu/tmpf2ik0u4a
Inference took 0.7859 seconds.
saved frontalized img
1/1 [==============================] - 0s 127ms/step


Action: race: 100%|██████████| 4/4 [00:01<00:00,  3.59it/s]   


male
AgingDataLoader
dataset [MulticlassUnalignedDataset] was created
Generator(
  (id_encoder): IdentityEncoder(
    (encoder): Sequential(
      (0): ReflectionPad2d((3, 3, 3, 3))
      (1): EqualConv2d(
        (conv): Conv2d(3, 64, kernel_size=(7, 7), stride=(1, 1))
      )
      (2): PixelNorm()
      (3): ReLU(inplace=True)
      (4): ReflectionPad2d((1, 1, 1, 1))
      (5): EqualConv2d(
        (conv): Conv2d(64, 128, kernel_size=(3, 3), stride=(2, 2))
      )
      (6): PixelNorm()
      (7): ReLU(inplace=True)
      (8): ReflectionPad2d((1, 1, 1, 1))
      (9): EqualConv2d(
        (conv): Conv2d(128, 256, kernel_size=(3, 3), stride=(2, 2))
      )
      (10): PixelNorm()
      (11): ReLU(inplace=True)
      (12): ResnetBlock(
        (conv_block): Sequential(
          (0): ReflectionPad2d((1, 1, 1, 1))
          (1): EqualConv2d(
            (conv): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1))
          )
          (2): PixelNorm()
          (3): ReLU(inplace=True)
  

saved aged faces /projectnb/sparkgrp/ml-atfal-mafkoda-grp/atfalmafkoda_unzip/database3/person78/frontslice_01_01.jpg
created temporary directory /scratch/7405901.1.cds-gpu/tmpn5rpstqs
1/1 [==============================] - 0s 34ms/step


Action: race: 100%|██████████| 4/4 [00:00<00:00, 17.15it/s]  


...

male
AgingDataLoader
dataset [MulticlassUnalignedDataset] was created
Generator(
  (id_encoder): IdentityEncoder(
    (encoder): Sequential(
      (0): ReflectionPad2d((3, 3, 3, 3))
      (1): EqualConv2d(
        (conv): Conv2d(3, 64, kernel_size=(7, 7), stride=(1, 1))
      )
      (2): PixelNorm()
      (3): ReLU(inplace=True)
      (4): ReflectionPad2d((1, 1, 1, 1))
      (5): EqualConv2d(
        (conv): Conv2d(64, 128, kernel_size=(3, 3), stride=(2, 2))
      )
      (6): PixelNorm()
      (7): ReLU(inplace=True)
      (8): ReflectionPad2d((1, 1, 1, 1))
      (9): EqualConv2d(
        (conv): Conv2d(128, 256, kernel_size=(3, 3), stride=(2, 2))
      )
      (10): PixelNorm()
      (11): ReLU(inplace=True)
      (12): ResnetBlock(
        (conv_block): Sequential(
          (0): ReflectionPad2d((1, 1, 1, 1))
          (1): EqualConv2d(
            (conv): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1))
          )
          (2): PixelNorm()
          (3): ReLU(inplace=True)
  

saved aged faces /projectnb/sparkgrp/ml-atfal-mafkoda-grp/atfalmafkoda_unzip/database3/person106/slice_01_01.png
path /projectnb/sparkgrp/ml-atfal-mafkoda-grp/atfalmafkoda_unzip/database3/person131/slice_01_01.jpg
created temporary directory /scratch/7405901.1.cds-gpu/tmpfhfiie3z
Number of faces detected: 1
here
shape <_dlib_pybind11.full_object_detection object at 0x2ab16a6ab1b0>
Aligned image has shape: (256, 256)
Inference took 0.0243 seconds.
saved frontalized img
1/1 [==============================] - 0s 18ms/step


Action: race: 100%|██████████| 4/4 [00:00<00:00, 17.70it/s]  


male
AgingDataLoader
dataset [MulticlassUnalignedDataset] was created
Generator(
  (id_encoder): IdentityEncoder(
    (encoder): Sequential(
      (0): ReflectionPad2d((3, 3, 3, 3))
      (1): EqualConv2d(
        (conv): Conv2d(3, 64, kernel_size=(7, 7), stride=(1, 1))
      )
      (2): PixelNorm()
      (3): ReLU(inplace=True)
      (4): ReflectionPad2d((1, 1, 1, 1))
      (5): EqualConv2d(
        (conv): Conv2d(64, 128, kernel_size=(3, 3), stride=(2, 2))
      )
      (6): PixelNorm()
      (7): ReLU(inplace=True)
      (8): ReflectionPad2d((1, 1, 1, 1))
      (9): EqualConv2d(
        (conv): Conv2d(128, 256, kernel_size=(3, 3), stride=(2, 2))
      )
      (10): PixelNorm()
      (11): ReLU(inplace=True)
      (12): ResnetBlock(
        (conv_block): Sequential(
          (0): ReflectionPad2d((1, 1, 1, 1))
          (1): EqualConv2d(
            (conv): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1))
          )
          (2): PixelNorm()
          (3): ReLU(inplace=True)
  

saved aged faces /projectnb/sparkgrp/ml-atfal-mafkoda-grp/atfalmafkoda_unzip/database3/person131/frontslice_01_01.jpg
created temporary directory /scratch/7405901.1.cds-gpu/tmppmk2auh7
1/1 [==============================] - ETA: 0s

absl-py==1.4.0
aiofiles==22.1.0
aiohttp==3.8.4
aiosignal==1.3.1
aiosqlite==0.19.0
altair==4.2.2
anyio==3.6.2
argon2-cffi==21.3.0
argon2-cffi-bindings==21.2.0
arrow==1.2.3
asttokens==2.2.1
astunparse==1.6.3
async-timeout==4.0.2
atila==0.26.11
attrs==22.2.0
Babel==2.12.1
backcall==0.2.0
bcrypt==4.0.1
beautifulsoup4==4.12.0
bleach==6.0.0
bokeh==3.1.0
cachetools==5.3.0
certifi==2022.12.7
cffi==1.15.1
charset-normalizer==2.1.1
click==8.1.3
cloudpickle==2.2.1
cmake==3.25.0
colorama==0.4.6
colour==0.1.5
comm==0.1.3
contourpy==1.0.7
cryptography==40.0.2
cuda-python==11.5.0
cv==1.0.0
cycler==0.11.0
Cython==0.29.34
dataclasses==0.6
datasets==2.10.1
debugpy==1.6.6
decorator==5.1.1
deepface==0.0.79
defusedxml==0.7.1
dill==0.3.6
dlib==19.24.1
dm-tree==0.1.8
dnn==0.7.4
dominate==2.7.0
efficientnet==1.0.0
entrypoints==0.4
executing==1.2.0
exif==1.6.0
fastapi==0.95.0
fastjsonschema==2.16.3
fdet==0.2.1
ffmpy==0.3.0
filelock==3.9.0
fire==0.5.0
Flask==2.2.3
flatbuffers==23.3.3
fonttools==4.39.2
fqdn==1.5